In [ ]:
import ee
ee.Initialize()

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import os
from shapely.geometry import Point, mapping, Polygon

In [ ]:
def gee_geometry_from_shapely(geom, crs='epsg:4326'):
    """ 
    Simple helper function to take a shapely geometry and a coordinate system and convert them to a 
    Google Earth Engine Geometry.
    """
    from shapely.geometry import mapping
    ty = geom.type
    if ty == 'Polygon':
        return ee.Geometry.Polygon(ee.List(mapping(geom)['coordinates']), proj=crs, evenOdd=False)
    elif ty == 'Point':
        return ee.Geometry.Point(ee.List(mapping(geom)['coordinates']), proj=crs)    
    elif ty == 'MultiPolygon':
        return ee.Geometry.MultiPolygon(ee.List(mapping(geom)['coordinates']), proj=crs, evenOdd=False)
    elif ty == 'MultiPoint':
        return ee.Geometry.MultiPoint(ee.List(mapping(geom)['coordinates']), proj=crs)
    
minx, maxx = -180, 180
miny, maxy = -60, 80

big_area = Polygon([[minx, maxy], [maxx, maxy], [maxx, miny], [minx, miny]])
polygon = gee_geometry_from_shapely(big_area)

In [ ]:
### Helper functions
def reduce_res(ic, out_crs, scale, agg_fx):
    '''
    Simple resolution reducer based on some aggregation function
    '''
    def red_(image):
        reduce_image = image.reduceResolution(reducer=agg_fx, maxPixels=65535)
        return reduce_image.reproject(crs=out_crs, scale=scale).set('system:time_start', image.get('system:time_start'))
    return ic.map(red_)

def kNDVI(image):
    '''
    Add a kNDVI band to an image
    '''
    ndvi2 = image.pow(2)
    kndvi = ndvi2.tan()
    return kndvi.set('system:time_start', image.get('system:time_start'))

def rescale(ic, scale, add=0):
    '''
    Rescale all images in an image collection by a given scale factor and addative factor. 
    ASSUMES ALL BANDS SCALED EQUALLY
    '''
    def r(image):
        return image.multiply(scale).add(add).set('system:time_start', image.get('system:time_start'))
    return ic.map(r)

def mask_images(ic, maskband, maskbit):
    '''
    Quick and dirty masking for MODIS data (or other simple contexts where the first QA bit is general)
    '''
    def mask_(image):
        qc = (1 << maskbit) #Bit 0 is the general quality flag
        qa = image.select(maskband) #Get the pixel QA band.
        mask = qa.bitwiseAnd(qc).eq(0)
        return image.updateMask(mask)
    return ic.map(mask_)

def rename(ic, name):
    '''
    Rename all images in a collection to a specified new name.
    '''
    def rn(image):
        return ee.Image(image).rename(name)
    return ic.map(rn)

def run_export(image, crs, filename, scale, region, folder=None, maxPixels=1e12, cloud_optimized=True):
    '''
    Runs an export function on GEE servers
    '''
    task_config = {'fileNamePrefix': filename,'crs': crs,'scale': scale,'maxPixels': maxPixels, 'fileFormat': 'GeoTIFF', 'formatOptions': {'cloudOptimized': cloud_optimized}, 'region': region,}
    if folder:
        task_config['folder'] = folder
    task = ee.batch.Export.image.toDrive(image, filename, **task_config)
    task.start()
    
def split_export(image, namebase, crs=None, scale=500, minx=-180, maxx=180, miny=-80, maxy=80, step=20, **kwaargs):
    '''
    Split a large (e.g., global) job into smaller pieces. Can help with memory issues/speed of processing.
    '''
    if not crs:
        crs = ee.Projection('EPSG:4326')
    for i in range(minx,maxx,step):
        for j in range(miny,maxy,step):
            imax = i + step
            jmax = j + step
            if jmax > maxy:
                jmax = maxy
            if imax > maxx:
                imax = maxx
            name = namebase + '_%i_%i_%i_%i_WGS84' % (i,imax,j,jmax)
    
            print('Starting', name)
            roi = ee.Geometry.Polygon([[i, j], [i, jmax], [imax, jmax], [imax, j]])
            run_export(image, crs=crs, filename=name, region=roi, scale=scale, **kwaargs)

In [ ]:
### DETRENDING METHODS
def piecewise_detrend(ic, start_year, end_year, fit_period=3):
    #Get the length of the sides from the fitting period
    len_sides = int((fit_period - 1) / 2)
    
    def create_yearlist(yr, len_sides):
        '''
        Create a list of years based on years before/after a given center year
        '''
        yearlist = [yr]
        for i in range(1,len_sides+1):
            yearlist.append(yr - i)
            yearlist.append(yr + i)
        yearlist.sort()
        return yearlist
    
    def multi_year_data(yearlist):
        '''
        For a list of years, return only that subset of the data
        '''
        flist = []
        for year in yearlist:
            flist.append(ee.Filter.calendarRange(year, year, 'year'))
        if len(flist) == 1:
            filt = flist[0]
        else:
            filt = ee.Filter.Or(flist)
        return filt
    
    output = []
    for year in range(start_year, end_year + 1):
        #Get this list of years to use as a filter
        yearlist = create_yearlist(year, len_sides)
        filt = multi_year_data(yearlist)
        
        #Subset the data and fit a harmonic of given order
        subset = ic.filter(filt)
        
        #Detrend that subset
        subset_dt = detrend(subset)
        
        #Retain only the given year
        filt = ee.Filter.calendarRange(year, year, 'year')
        dt_year = subset_dt.filter(filt)
        output.append(dt_year)
    
    #Merge the years of data back together
    base = output[0]
    for i in output[1:]:
        base = base.merge(i)
    return base

def detrend_nonlin(collection, order=3):    
    def addVariables(image):
        date = ee.Date(image.get('system:time_start'))
        years = date.difference(ee.Date('1970-01-01'), 'year')
        t = ee.Image(years).rename('t')
        t2 = ee.Image(years).pow(ee.Image(2)).rename('t2').toFloat()
        t3 = ee.Image(years).pow(ee.Image(3)).rename('t3').toFloat()
        t4 = ee.Image(years).pow(ee.Image(4)).rename('t4').toFloat()
        t5 = ee.Image(years).pow(ee.Image(5)).rename('t5').toFloat()
        t6 = ee.Image(years).pow(ee.Image(6)).rename('t6').toFloat()
        t7 = ee.Image(years).pow(ee.Image(7)).rename('t7').toFloat()
        t8 = ee.Image(years).pow(ee.Image(8)).rename('t8').toFloat()
        return image.addBands(ee.Image.constant(1)).addBands(t).addBands(t2)\
                .addBands(t3).addBands(t4).addBands(t5).addBands(t6).addBands(t7).addBands(t8).float()

    idps = ['constant', 't', 't2', 't3', 't4', 't5', 't6', 't7', 't8']
    idps = idps[:order+1]
    independents = ee.List(idps)
    img = collection.first()
    bn = img.bandNames().get(0)
    dependent = ee.String(bn)
    
    coll = collection.map(addVariables)
    
    #Compute a linear trend.  This will have two bands: 'residuals' and 
    #a 2x1 band called coefficients (columns are for dependent variables).
    trend = coll.select(independents.add(dependent)).reduce(ee.Reducer.linearRegression(independents.length(), 1))
    
    #Flatten the coefficients into a 2-band image
    coefficients = trend.select('coefficients').arrayProject([0]).arrayFlatten([independents])
    
    #Compute a de-trended series.
    def remove_trend(image):
        detrended = image.select(dependent).subtract(image.select(independents).multiply(coefficients).reduce('sum'))\
            .rename('detrend').copyProperties(image, ['system:time_start'])
        return image.addBands(detrended)
    
    detrended = coll.map(remove_trend)
    return detrended.select('detrend')

def rolling_detrend(ic, fit_period=5, window_unit='year', var=None):
    '''
    Apply a function over a moving window
    '''
    if var:
        ic = ic.select(var)
        
    if window_unit == 'year':
        fit_period = fit_period * 365
        window_unit = 'day'

    len_sides = int((fit_period - 1) / 2)

    def apply_roller(dates):
        def roller(t):
            t = ee.Date(t) #Get the date
            #Use the date to create a search window of windowSize in both directions
            window = ic.filterDate(t.advance(-len_sides,window_unit),t.advance(len_sides,window_unit))
            
            #Detrend over that window
            dt = detrend(window)
            
            #Select only the center date
            img = ee.Image(dt.filterDate(t).first())
            
            return img.set('system:time_start', t).rename('dt').float()
        
        vals = dates.map(roller)
        return vals
    
    dates = ee.List(ic.aggregate_array('system:time_start'))
    vals = apply_roller(dates)
    
    return ee.ImageCollection.fromImages(vals)

def rolling_mean(ic, fit_period=5, window_unit='year', var=None, fp=None):
    '''
    Apply a function over a moving window
    '''
    if var:
        ic = ic.select(var)
        
    if window_unit == 'year':
        fit_period = fit_period * 365
        window_unit = 'day'
        
    len_sides = int((fit_period - 1) / 2)
    
    def apply_roller(dates):
        def roller(t):
            t = ee.Date(t) #Get the date
            #Use the date to create a search window of windowSize in both directions
            window = ic.filterDate(t.advance(-len_sides,window_unit),t.advance(len_sides,window_unit))
            
            def add_fp(image):
                return image.set('system:footprint', fp).float()
            
            if fp: #Note -- this can be used for synthetic data, which may lack a proper geometry
                window = window.map(add_fp)
            
            #Get the mean over the window
            img = window.reduce(ee.Reducer.mean()).float()
            
            #Select original data the center date
            data = ee.Image(window.filterDate(t).first())
            
            #Subtract
            out = data.subtract(img)
            out = out.set('system:time_start', t).rename('dt').float()
            if fp:
                out = out.set('system:footprint', fp)
            return out
        
        vals = dates.map(roller)
        return vals
    
    dates = ee.List(ic.aggregate_array('system:time_start'))
    vals = apply_roller(dates)
    
    return ee.ImageCollection.fromImages(vals)

In [ ]:
### DESEASONING METHODS
def remove_lt_daily_mean(ic, fp=None):
    set_of_anoms = []
    for day in range(1,365):
        filt = ee.Filter.dayOfYear(day,day)
        subset = ic.filter(filt)
        lt_mean = ee.Image(subset.reduce(ee.Reducer.mean()))
        if fp:
            lt_mean = lt_mean.set('system:footprint', fp)
        
        def rm_(image):
            dif = image.subtract(lt_mean)
            if fp:
                dif = dif.set('system:footprint', fp)
            return dif.set('system:time_start', image.get('system:time_start'))
        
        anoms = ee.ImageCollection(subset.map(rm_))
        set_of_anoms.append(anoms)
    
    output = set_of_anoms[0]
    for i in set_of_anoms[1:]:
        output = output.merge(i)
        
    #Finally, sort the results
    output = output.sort('system:time_start')
    return output

def fit_multi_harmonic(collection, harmonics=3, bn=None):
    """
    Function to fit a complex harmonic model to an ImageCollection. Uses any number of desired harmonics. 
    Original function adapted from:
    https://code.earthengine.google.com/2669122497313113fc4bb81bc8352828
    
    Returns the harmonic-smoothed dataset, the phase of the harmonic, the amplitude of the harmonic
    and a simple R squared value for the fit. 

    """
    import numpy as np

    #Get the name of the image band
    if not bn:
        img = collection.first()
        #bn = img.bandNames().getInfo()[0]
        bn = img.bandNames().get(0)

    #Get list of harmonic terms
    harmonicFrequencies = list(range(1, harmonics+1))#ee.List.sequence(1, harmonics)
    
    def getNames(base_bn, l):
        out = []
        for i in l:
            out.append(base_bn + str(i))
        return ee.List(out)
    
    #Construct lists of names for the harmonic terms.
    cosNames = getNames('cos_', harmonicFrequencies)
    sinNames = getNames('sin_', harmonicFrequencies)
    
    #Add the list of all sin/cos terms to the independent variables list
    independents = ee.List(['constant', 't']).cat(cosNames).cat(sinNames)
    
    def addVariables(image):
        date = ee.Date(image.get('system:time_start'))
        years = date.difference(ee.Date('1970-01-01'), 'year')
        #THE HARMONICS ARE FIT IN UNITS OF TIME (in this case, years)
        timeRadians = ee.Image(years.multiply(2 * np.pi))
        return image.addBands(timeRadians.rename('t').float()).addBands(ee.Image.constant(1))
        
    #Function to compute the specified number of harmonics and add them as bands.  
    #Assumes the time band is present.
    def addHarmonics(freqs):
        #This returns a function to be mapped over the ImageCollection, adding all required bands
        def fx(image):
            #Make an image of frequencies.
            frequencies = ee.Image.constant(freqs)
            #This band should represent time in radians.
            time = ee.Image(image).select('t')
            #Get the cosine terms.
            cosines = time.multiply(frequencies).cos().rename(cosNames)
            #Get the sine terms
            sines = time.multiply(frequencies).sin().rename(sinNames)
            return image.addBands(cosines).addBands(sines)
        return fx
    
    #Add the time and constant bands
    coll = collection.map(addVariables)
    #Add the arbitrary number of sin/cos bands
    harmonic_coll = coll.map(addHarmonics(harmonicFrequencies))
    
    #The output of the regression reduction is a 4x1 array image.
    harmonicTrend = harmonic_coll.select(independents.add(bn)).reduce(ee.Reducer.linearRegression(independents.length(), 1))
    
    #Turn the array image into a multi-band image of coefficients.
    harmonicTrendCoefficients = harmonicTrend.select('coefficients').arrayProject([0]).arrayFlatten([independents])
    #This has individual coefficents for each frequency (plus t and constant)

    #Compute fitted values.
    def add_harm_fitted(image):
        return image.addBands(image.select(independents).multiply(harmonicTrendCoefficients).reduce('sum').rename('fitted'))
    
    #This will return one fitted line -- the sum of all harmonic terms
    fittedHarmonic = harmonic_coll.map(add_harm_fitted)

    def phase_from_harmonic(harmonicTrendCoefficients, number):
        #Compute phase and amplitude.
        phase = harmonicTrendCoefficients.select('sin_' + str(number)).atan2(harmonicTrendCoefficients.select('cos_' + str(number))).rename('phase_' + str(number)) #.unitScale(-np.pi, np.pi)
        amplitude = harmonicTrendCoefficients.select('sin_' + str(number)).hypot(harmonicTrendCoefficients.select('cos_' + str(number))).rename('amplitude_' + str(number))
        
        return ee.Image(phase), ee.Image(amplitude)
    
    #To return all phase/amplitude values, loop over the number of sin/cos terms
    multiphase, multiamp = [], []
    for i in harmonicFrequencies:
        phase, amplitude = phase_from_harmonic(harmonicTrendCoefficients, i)
        multiphase.append(phase.toFloat())
        multiamp.append(amplitude.toFloat())
        
    #Convert these lists into multiband images for easier processing/exporting
    multiphase = ee.ImageCollection.fromImages(multiphase).toBands()
    multiamp = ee.ImageCollection.fromImages(multiamp).toBands()

    #Get Model fit
    def distance_to_orig(image):
        resids = image.select('fitted').subtract(image.select(bn))
        ss_res = resids.pow(ee.Number(2)).rename('SumSQ')
        dist_mean = image.select(bn).subtract(mn)
        ss_tot = dist_mean.pow(ee.Number(2)).rename('DistMean')
        #rsq = 1 - (ss_res / ss_tot)
        
        return image.addBands(ss_res).addBands(ss_tot)
    
    mn = collection.reduce(ee.Reducer.mean())
    distfit = fittedHarmonic.map(distance_to_orig)
    
    #Sum of Resids
    sum_resids = distfit.select('SumSQ').reduce(ee.Reducer.sum())
    sum_sqtot = distfit.select('DistMean').reduce(ee.Reducer.sum())
    
    #Divide the summed images and subtract from 1 for a classic RSQ value
    rsq = ee.Image(1).subtract(sum_resids.divide(sum_sqtot)).rename('RSQ')

    return fittedHarmonic.select('fitted'), multiphase, multiamp, rsq

def moving_harmonic(ic, start_year, end_year, bn=None, fit_period=3, harmonic_order=3):
    '''
    Fit a harmonic in multiple parts -- can be done year by year, or by fitting the harmonics to a 
    given multi-year time window. Fit period must be odd (or zero)!
    '''
    
    #Get the length of the sides from the fitting period
    len_sides = int((fit_period - 1) / 2)
    
    def create_yearlist(yr, len_sides):
        '''
        Create a list of years based on years before/after a given center year
        '''
        yearlist = [yr]
        for i in range(1,len_sides+1):
            yearlist.append(yr - i)
            yearlist.append(yr + i)
        yearlist.sort()
        return yearlist
    
    def multi_year_data(yearlist):
        '''
        For a list of years, return only that subset of the data
        '''
        flist = []
        for year in yearlist:
            flist.append(ee.Filter.calendarRange(year, year, 'year'))
        if len(flist) == 1:
            filt = flist[0]
        else:
            filt = ee.Filter.Or(flist)
        return filt
    
    output = []
    for year in range(start_year, end_year + 1):
        yearlist = create_yearlist(year, len_sides)
        filt = multi_year_data(yearlist)
        
        #Subset the data and fit a harmonic of given order
        subset = ee.ImageCollection(ic.filter(filt))
        
        #Detrend that subset
        #subset_dt = detrend(subset)
        harmonic, phase, amplitude, rsq = fit_multi_harmonic(subset, harmonics=harmonic_order, bn=bn)
        
        #Retain only the given year
        filt = ee.Filter.calendarRange(year, year, 'year')
        harmonic_year = harmonic.filter(filt)
        output.append(harmonic_year)
    
    #Merge the years of data back together
    base = output[0]
    for i in output[1:]:
        base = base.merge(i)
    return base

In [ ]:
def join_c(c1, c2, on='system:index'):
    '''
    Quick and dirty join on an arbitrary field. 
    '''
    filt = ee.Filter.equals(leftField=on, rightField=on) 
    innerJoin = ee.Join.inner() #initialize the join
    innerJoined = innerJoin.apply(c1, c2, filt) #This is a FEATURE COLLECTION
    def combine_joined(feature):
        return ee.Image.cat(feature.get('primary'), feature.get('secondary'))
    
    joined_collect = ee.ImageCollection(innerJoined.map(combine_joined))
    return joined_collect

def simple_difference(ic, b1, b2, outname='dif'):
    '''
    Simple difference between two bands in an image collection
    '''
    def sub(image):
        i1 = image.select(b1)
        i2 = image.select(b2)
        return i1.subtract(i2).rename(outname).set('system:time_start', image.get('system:time_start')).set('system:footprint', image.get('system:footprint'))
    return ic.map(sub)

def deseason_data(ic, bn=None, detrend_type='rolling_mean', deseason=True, detrend_fit_period=5, detrend_order=3, \
                  harmonic='single', start_year=2000, end_year=2022, \
                  harmonic_fit_period=3, harmonic_order=3, fp=None):
    '''
    Top-level for de-seasoning data. Takes multiple options for detrending and deseasoning. 
    '''
    if not bn:
        img = ic.first()
        bn = img.bandNames().get(0)
     
    #Get rid of linear trends
    if detrend_type == 'single':
        detrend_ic = detrend(ic) #This is a simple non-moving detrender
    elif detrend_type == 'piecewise':
        detrend_ic = piecewise_detrend(ic, start_year, end_year, detrend_fit_period) #Fit 5-year ramps to detrend, three years for harmonics
    elif detrend_type == 'rolling_lmfit': #Rolling linear fit
        detrend_ic = rolling_detrend(ic, fit_period=detrend_fit_period, window_unit='year')
    elif detrend_type == 'nonlinear': #Nonlinear detrender via fitting a high-order polynomial
        detrend_ic = detrend_nonlin(ic, order=detrend_order)
    elif detrend_type == 'rolling_mean': #Rolling mean
        detrend_ic = rolling_mean(ic, fit_period=detrend_fit_period, fp=fp)
    else:
        detrend_ic = ic #Can also skip the detrending
        
    if deseason:
        #Find the seasonal component
        if harmonic == 'single':
            harmonic, _, _, _ = fit_multi_harmonic(detrend_ic, harmonics=harmonic_order)
        elif harmonic == 'moving':
            harmonic = moving_harmonic(detrend_ic, start_year, end_year, fit_period=harmonic_fit_period, harmonic_order=harmonic_order)

        #Rename the detrended data as dt
        dt = rename(detrend_ic, 'dt')

        #Get seasonality via harmonics
        seasonality = rename(harmonic, 'seas')

        #Subtract the seasonal signal from the detrended signal to produce the final residuals
        joint_vals = join_c(dt, seasonality, on='system:time_start')
        deseasoned = simple_difference(joint_vals, 'dt', 'seas')

        deseasoned = rename(deseasoned, 'ds')
    else:
        deseasoned = rename(detrend_ic, 'ds')
    
    return deseasoned

def do_deseason(ic):
    #V0: No deseason, rolling mean detrend
    v0 = deseason_data(ic, deseason=False, detrend_type='rolling_mean')
    
    #V1: No deseason, rolling linear fit detrend
    v1 = deseason_data(ic, deseason=False, detrend_type='rolling_lmfit')

    #V2: Detrend via rolling mean, then single harmonic for full TS, order = 3
    v2 = deseason_data(ic, deseason=True, harmonic='single', harmonic_order=3, detrend_type='rolling_mean')
    
    #V3: Detrend via linear fit, then single harmonic for full TS, order = 3
    v3 = deseason_data(ic, deseason=True, harmonic='single', harmonic_order=3, detrend_type='rolling_lmfit')

    return v0, v1, v2, v3

In [ ]:
def lambda_gee(ic, robust=True):
    '''
    This provides two means of getting at autocorrelation, as well as \lambda and \sigma via
    [x vs xt+1] and [x vs dx]

    '''
    ic = ee.ImageCollection(ic) #Make sure the data type is properly cast
    l = ic.toList(ic.size()) #Convert the set of images into a list for slicing

    dt = l.slice(0,l.size().subtract(1)) #Slice x from position 0 to [-2]    
    dtp1 = l.slice(1,l.size()) #Slice x from position 1 to [-1]
    
    def create_collection(i):
        x0 = ee.Image(dt.get(i)).rename('xt').set('system:index', ee.Number(i).format('%s'))
        x1 = ee.Image(dtp1.get(i)).rename('xtp1').set('system:index', ee.Number(i).format('%s'))
        dx = ee.Image(x1.subtract(x0)).rename('dx').set('system:index', ee.Number(i).format('%s'))
        constant = ee.Image(1).rename('constant').set('system:index', ee.Number(i).format('%s'))
        return constant.addBands(x0).addBands(x1).addBands(dx)
    
    seq = ee.List.sequence(0, dt.size().subtract(1)) #Create a sequence running from 0-len(x)
    data = ee.ImageCollection.fromImages(seq.map(create_collection)) #Create the set of images that are xt,xtp1,dx,constant
    
    #Now using that joined collection, do a regression
    if robust:
        fit = data.select(['constant', 'xt', 'dx']).reduce(ee.Reducer.robustLinearRegression(numX=2, numY=1))
    else:
        fit = data.select(['constant', 'xt', 'dx']).reduce(ee.Reducer.linearRegression(numX=2, numY=1))
    slope_kappa = fit.select(['coefficients']).arrayProject([0]).arrayFlatten([['constant', 'trend']]).select('trend')
    
    if robust: #Note that this is lag-1 autocorrelation
        fit = data.select(['constant', 'xt', 'xtp1']).reduce(ee.Reducer.robustLinearRegression(numX=2, numY=1))
    else:
        fit = data.select(['constant', 'xt', 'xtp1']).reduce(ee.Reducer.linearRegression(numX=2, numY=1))
    slope_xt = fit.select(['coefficients']).arrayProject([0]).arrayFlatten([['constant', 'trend']]).select('trend')
    
    #Convert to recovery rate \lambda
    kappa_fix = slope_kappa.add(1)
    lambda_kappa = kappa_fix.log().rename('lambda_kappa')
    
    lambda_xt = slope_xt.log().rename('lambda_xt')
    
    #Create standard residuals via (dx - trend*x)
    def create_resid_kappa(image):
        resid = image.select('dx').subtract(image.select('xt').multiply(slope_kappa)).rename('resid')
        return resid
    
    resid_kappa = data.map(create_resid_kappa)
    sigma_kappa = resid_kappa.reduce(ee.Reducer.stdDev())
    
    def create_resid_xt(image):
        resid = image.select('xtp1').subtract(image.select('xt').multiply(slope_xt)).rename('resid')
        return resid
    
    resid_xt = data.map(create_resid_xt)
    sigma_xt = resid_xt.reduce(ee.Reducer.stdDev())
    
    return slope_kappa, slope_xt, lambda_kappa, lambda_xt, sigma_kappa, sigma_xt

def get_lt_lambda(ic):
    '''
    Get the two estmimates of lambda over the full image collection
    '''
    _, _, _, lambda_xt, _, sigma_xt = lambda_gee(ic, robust=True)
    lt_var = ic.reduce(ee.Reducer.variance(), 4)
    ex = ee.Image(1).subtract(sigma_xt.pow(2).divide(lt_var)) 
    lambda_variance = ex.log().multiply(0.5)
    return lambda_xt, lambda_variance

In [ ]:
#Load in EVI data and remove low-quality measurements
ds, de = '2000-10-01', '2022-10-01' #Second date is EXCLUSIVE, match start of resampled RAD to LST/NDVI

MOD13_250 = ee.ImageCollection("MODIS/061/MOD13Q1").filterDate(ds, de) #THIS IS 250m DATA
MOD13_250_hq = mask_images(MOD13_250, 'SummaryQA', 0)
evi_250 = MOD13_250_hq.select('EVI')
evi_250 = rescale(evi_250, 0.0001)
ndvi_250 = MOD13_250_hq.select('NDVI')
ndvi_250 = rescale(ndvi_250, 0.0001)
kndvi_250 = ndvi_250.map(kNDVI)

MOD13_1k = ee.ImageCollection("MODIS/061/MOD13A2").filterDate(ds, de) #THIS IS 1KM DATA
MOD13_1k_hq = mask_images(MOD13_1k, 'SummaryQA', 0)
evi_1k = MOD13_1k_hq.select('EVI')
evi_1k = rescale(evi_1k, 0.0001)
ndvi_1k = MOD13_1k_hq.select('NDVI')
ndvi_1k = rescale(ndvi_1k, 0.0001)
kndvi_1k = ndvi_1k.map(kNDVI)

crs = ee.Projection('EPSG:4326')
mod_crs = ndvi_250.first().projection()

evi_5k = reduce_res(evi_1k, mod_crs, 5000, ee.Reducer.mean())
ndvi_5k = reduce_res(ndvi_1k, mod_crs, 5000, ee.Reducer.mean())
kndvi_5k = reduce_res(kndvi_1k, mod_crs, 5000, ee.Reducer.mean())

evi_10k = reduce_res(evi_1k, mod_crs, 10000, ee.Reducer.mean())
ndvi_10k = reduce_res(ndvi_1k, mod_crs, 10000, ee.Reducer.mean())
kndvi_10k = reduce_res(kndvi_1k, mod_crs, 10000, ee.Reducer.mean())

evi_25k = reduce_res(evi_1k, mod_crs, 25000, ee.Reducer.mean())
ndvi_25k = reduce_res(ndvi_1k, mod_crs, 25000, ee.Reducer.mean())
kndvi_25k = reduce_res(kndvi_1k, mod_crs, 25000, ee.Reducer.mean())

In [ ]:
to_proc = {'kNDVI_5k':[kndvi_5k, 5000],'NDVI_5k':[ndvi_5k, 5000], 'EVI_5k':[evi_5k, 5000]}
folder = 'Lambda_5k'

crs = ee.Projection('EPSG:4326') #Save the output as WGS84 for ease of use
for data in to_proc.keys():
    ic, scale = to_proc[data]
    v0, v1, v2, v3 = do_deseason(ic) #Deseason/detrend the data
    lambda_xt, lambda_variance = get_lt_lambda(v2) #Use the rolling mean deseasoner to get the lambdas
    
    ar_name = data + '_V2_lambdaXT'
    if not os.path.exists(data_folder + ar_name + '.tif'):
        run_export(lambda_xt, crs, ar_name, scale=scale, region=polygon, folder=folder)
        #split_export(lambda_xt, namebase=ar_name, crs=crs, scale=scale, folder=ar_name,\
        #     minx=-180, maxx=180, miny=-60, maxy=80, step=5)
    
    var_name = data + '_V2_lambdaVAR'
    if not os.path.exists(data_folder + var_name + '.tif'):
        run_export(lambda_variance, crs, var_name, scale=scale, region=polygon, folder=folder)
        #split_export(lambda_variance, namebase=var_name, crs=crs, scale=scale, folder=var_name,\
        #         minx=-180, maxx=180, miny=-60, maxy=80, step=5)

In [ ]:
#Add in GPP
MOD17 = ee.ImageCollection("MODIS/006/MOD17A2H").filterDate(ds, de)
MOD17_hq = mask_images(MOD17, 'Psn_QC', 0)
GPP = MOD17_hq.select('Gpp')
GPP = rescale(GPP, 0.0001) #Native 500m data

crs = ee.Projection('EPSG:4326')
mod_crs = GPP.first().projection() #Use this coordinate system for the spatial aggregation

gpp_1k = reduce_res(GPP, mod_crs, 1000, ee.Reducer.mean())
gpp_5k = reduce_res(GPP, mod_crs, 5000, ee.Reducer.mean())
gpp_10k = reduce_res(GPP, mod_crs, 10000, ee.Reducer.mean())
gpp_25k = reduce_res(GPP, mod_crs, 25000, ee.Reducer.mean())

to_proc = {'GPP_5k':[gpp_5k, 5000]}#,'GPP_1k':[gpp_1k, 1000], 'GPP_10k':[gpp_10k, 10000]}
folder = 'GPP_Lambda'
crs = ee.Projection('EPSG:4326')

#Export as above

In [ ]:
#Add in LAI
ds_lai, de_lai = '2002-10-01', '2022-10-01'
MOD15 = ee.ImageCollection("MODIS/061/MCD15A3H").filterDate(ds_lai, de_lai)
MOD15_hq = mask_images(MOD15, 'FparLai_QC', 0)
lai = MOD15_hq.select('Lai')
lai = rescale(lai, 0.1) #Native 500m data

crs = ee.Projection('EPSG:4326')
mod_crs = lai.first().projection() #Use this coordinate system for the spatial aggregation

lai_1k = reduce_res(lai, mod_crs, 1000, ee.Reducer.mean())
lai_5k = reduce_res(lai, mod_crs, 5000, ee.Reducer.mean())
lai_10k = reduce_res(lai, mod_crs, 10000, ee.Reducer.mean())
lai_25k = reduce_res(lai, mod_crs, 25000, ee.Reducer.mean())

to_proc = {'LAI_5k':[lai_5k, 5000]}#,'GPP_1k':[gpp_1k, 1000], 'GPP_10k':[gpp_10k, 10000]}
folder = 'LAI_Lambda'
crs = ee.Projection('EPSG:4326')

#Export as above

In [ ]:
### Now to get trends
def lambda_trend(ic, first_year=2002, last_year=2020, window=2, kt=False, trend=False): 
    '''
    Takes in deseasoned/detrended data, then gets a value per year. Uses that to do regression, 
    either via Linear or KendallTau
    '''
    save = []
    for yr in range(first_year, last_year + 1):
        sy, ey = yr - window, yr + window #Create a window around the central year
        sd, ed = ee.Date(str(sy) + '-10-01'), ee.Date(str(ey) + '-10-01') #Clip out water-years (oct-oct)
        subset = ic.filterDate(sd, ed)
        out_date = ee.Date(str(ey) + '-04-01')
        
        #Create a constant to make regressions with later
        const = ee.Image.constant(1).rename('constant').set('system:time_start', out_date).float()
        gap = subset.reduce(ee.Reducer.count(), 4).rename('count').set('system:time_start', out_date).float()
        mask = gap.gt(15) #Mask out points with less than 15 measurements over 5 years
        
        lambda_xt, lambda_variance = get_lt_lambda(subset)
        base_yr = ee.Image(yr).rename('year').set('system:time_start', out_date).float()
        
        #Mask out lambda/variance values that are based on less than 15 points
        lambda_xt = lambda_xt.rename('lambda_ac1').set('system:time_start', out_date).float().updateMask(mask)
        lambda_variance = lambda_variance.rename('lambda_var').set('system:time_start', out_date).float().updateMask(mask)
        
        #Create one multiband image
        output = const.addBands(base_yr).addBands(gap).addBands(lambda_xt).addBands(lambda_variance)
        save.append(output.set('system:time_start', out_date))
    
    #Turn everything into a single collection
    save = ee.ImageCollection.fromImages(save)
    
    if trend:
        #Now do some regressions
        fit = save.select(['constant', 'year', 'count']).reduce(ee.Reducer.robustLinearRegression(numX=2, numY=1))
        slope_count = fit.select(['coefficients']).arrayProject([0]).arrayFlatten([['constant', 'trend']]).select('trend')
        
        fit = save.select(['constant', 'year', 'lambda_ac1']).reduce(ee.Reducer.robustLinearRegression(numX=2, numY=1))
        slope_ac1 = fit.select(['coefficients']).arrayProject([0]).arrayFlatten([['constant', 'trend']]).select('trend')

        fit = save.select(['constant', 'year', 'lambda_var']).reduce(ee.Reducer.robustLinearRegression(numX=2, numY=1))
        slope_var = fit.select(['coefficients']).arrayProject([0]).arrayFlatten([['constant', 'trend']]).select('trend')

        return slope_count, slope_ac1, slope_var
    
    if kt:
        #NOTE - P-values are not working via GEE  https://issuetracker.google.com/issues/245531512?pli=1
        count_tau = save.select(['year', 'count']).reduce(ee.Reducer.kendallsCorrelation(2), 4) #Bump up the parallel scale
        ac1_tau = save.select(['year', 'lambda_ac1']).reduce(ee.Reducer.kendallsCorrelation(2), 4)
        var_tau = save.select(['year', 'lambda_var']).reduce(ee.Reducer.kendallsCorrelation(2), 4)
        
        return count_tau, ac1_tau, var_tau

In [ ]:
crs = ee.Projection('EPSG:4326')
data = 'EVI_5k' #Replace with other indices
folder = data + '_Trend'
ic, scale = evi_5k, 5000 #Replace with other indices or resolutions
v0, v1, v2, v3 = do_deseason(ic) #Deseason/detrend the data as above

count_tau, ac1_tau, var_tau = lambda_trend(v2, kt=True)
slope_count, slope_ac1, slope_var = lambda_trend(v2, trend=True)

run_export(slope_ac1, crs, data + '_AC1_OLS', scale=scale, region=polygon, folder=folder)
run_export(slope_var, crs, data + '_VAR_OLS', scale=scale, region=polygon, folder=folder)
run_export(slope_count, crs, data + '_Count_OLS', scale=scale, region=polygon, folder=folder)

run_export(ac1_tau, crs, data + '_AC1_tau', scale=scale, region=polygon, folder=folder)
run_export(var_tau, crs, data + '_VAR_tau', scale=scale, region=polygon, folder=folder)
run_export(count_tau, crs, data + '_Count_tau', scale=scale, region=polygon, folder=folder)